In [1]:
import os,datetime
import cv2
import xml.etree.ElementTree as ET
from PIL import Image
import numpy as np
import random
from pathlib import Path

time_str = (datetime.datetime.now()).strftime("%Y%m%d")
time_str = '20190507'
xml_dir = '/data/darknet/python/' + time_str + '_xml/'
image_dir = '/data/darknet/python/' + time_str + '_image/'
#generated_image_dir = image_dir
#generated_xml_dir = xml_dir

generated_image_dir = '/data/darknet/python/' + time_str + '_image_expand_obj/'
generated_xml_dir = '/data/darknet/python/' + time_str + '_xml_expand_obj/'

#os.system('mkdir -p ' + xml_dir)
#os.system('mkdir -p ' + image_dir)
os.system('mkdir -p ' + generated_image_dir)
os.system('mkdir -p ' + generated_xml_dir)

SEED_XML_DIR = xml_dir
SEED_IMG_DIR = image_dir
GENE_IMG_DIR = generated_image_dir
GENE_XML_DIR = generated_xml_dir


# RT:RightTop 
# LB:LeftBottom 
# bbox: [xmin, xax, ymin, ymax]
def IOU(bbox_a, bbox_b):
    '''
    W = min(A.RT.x, B.RT.x) - max(A.LB.x, B.LB.x) 
    H = min(A.RT.y, B.RT.y) - max(A.LB.y, B.LB.y) 
    if W <= 0 or H <= 0: 
        return 0 
    SA = (A.RT.x - A.LB.x) * (A.RT.y - A.LB.y) 
    SB = (B.RT.x - B.LB.x) * (B.RT.y - B.LB.y) 
    cross = W * H return cross/(SA + SB - cross)
    '''
    W = min(bbox_a[1], bbox_b[1]) - max(bbox_a[0], bbox_b[0]) 
    H = min(bbox_a[3], bbox_b[3]) - max(bbox_a[2], bbox_b[2]) 
    if W <= 0 or H <= 0: 
        return 0
    SA = (bbox_a[1] - bbox_a[0]) * (bbox_a[3] - bbox_a[2]) 
    SB = (bbox_b[1] - bbox_b[0]) * (bbox_b[3] - bbox_b[2])  
    cross = W * H 
    return cross/(SA + SB - cross)

def get_bbox_from_xmlobj(obj_element):
    xmlbox = obj_element.find('bndbox')
    return [float(xmlbox.find('xmin').text), float(xmlbox.find('xmax').text), 
            float(xmlbox.find('ymin').text), float(xmlbox.find('ymax').text)]

def get_obj_from_xml(xml):
    in_file = open(xml_name)
    tree=ET.parse(in_file)
    root = tree.getroot()
    return [obj for obj in root.iter('object')]

def get_obj_from_image_file(file, bbox):
    img = cv2.imread(file)
    img_obj = img[int(bbox[2]):int(bbox[3]), int(bbox[0]):int(bbox[1])]
    print(img_obj.shape)
    return img_obj

def get_bboxes_from_etree(etree):
    root = etree.getroot()  
    objects = root.findall('object')
    bboxes = []
    for obj in objects:
        xmlbox = obj.find('bndbox')
        b = [float(xmlbox.find('xmin').text), float(xmlbox.find('xmax').text), float(xmlbox.find('ymin').text), float(xmlbox.find('ymax').text)]
        bboxes.append(b)
    return bboxes
def past_to_background_from_image_file(file, bboxes, background_img_array, extend_spaces=0):
    
    img = cv2.imread(file)
    #img = img - 50
    if(img.shape != background_img_array.shape):
        print('shape not match')
        return
    #print(img.shape)
    #print(img)
    img_objs = []
    for bbox in bboxes:
        img_obj = img[int(bbox[2]):int(bbox[3]), int(bbox[0]):int(bbox[1])]
        img_objs.append(img_obj)
    i = 0
    for bbox in bboxes:
        background_img_array[int(bbox[2]):int(bbox[3]), int(bbox[0]):int(bbox[1])] = img_objs[i]
        i = i+1
    cv2.imwrite(GENE_IMG_DIR+file.split('/')[-1], background_img_array)
    return 
def generate_new_xmlobj(xmlobj_old, new_position, new_size):
    element_object = ET.Element('object')
    tag_name = ET.SubElement(element_object, 'name')
    tag_name.text = xmlobj_old.find('name').text

    tag_difficult = ET.SubElement(element_object, 'difficult')
    tag_difficult.text = xmlobj_old.find('difficult').text

    element_bndbox = ET.SubElement(element_object, 'bndbox')
    tag_xmin = ET.SubElement(element_bndbox, 'xmin')
    tag_ymin = ET.SubElement(element_bndbox, 'ymin')
    tag_xmax = ET.SubElement(element_bndbox, 'xmax')
    tag_ymax = ET.SubElement(element_bndbox, 'ymax')
    tag_xmin.text = str(new_position[0])
    tag_ymin.text = str(new_position[1])
    tag_xmax.text = str(new_position[0] + new_size[1])
    tag_ymax.text = str(new_position[1] + new_size[0])
    return element_object
    
def past_and_insert(img_obj, img_array, new_position, obj_element, etree):
    new_xmlobj = generate_new_xmlobj(obj_element, new_position, img_obj.shape[:2])
    new_xml_etree = insert_to_xml(new_xmlobj, etree)
    new_pil_img = past_obj_to_background(img_obj, img_array, new_position)
    return new_pil_img, new_xml_etree
    

def insert_to_xml(xml_obj, xml_etree):
    root = xml_etree.getroot()
    root.append(xml_obj)
    return xml_etree
    
def past_obj_to_background(img_obj, img_array, position = (200, 200)):
    img = Image.fromarray(img_array)
    img_obj = Image.fromarray(img_obj)
    img.paste(img_obj, position)
    return img
    
def get_cls_from_xmlobj(obj_element):    
    return obj_element.find('name').text

def generate_new_position(img_size, img_obj_size):
    array_x = np.arange(int(img_size[1] - img_obj_size[1]))
    array_y = np.arange(int(img_size[0] - img_obj_size[0]))
    random_x = random.sample(list(array_x), 1)[0]
    random_y = random.sample(list(array_y), 1)[0]
    new_position = (random_x, random_y)
    #print(new_position)
    return new_position

def generate_new_bbox(img_size, img_obj_size):
    array_x = np.arange(int(img_size[1] - img_obj_size[1]))
    array_y = np.arange(int(img_size[0] - img_obj_size[0]))
    random_x = random.sample(list(array_x), 1)[0]
    random_y = random.sample(list(array_y), 1)[0]
    new_position = (random_x, random_y)
    new_bbox = [random_x, random_x + img_obj_size[1], random_y, random_y + img_obj_size[0]]
    #print(new_bbox)
    return new_bbox
def generate_union_bbox(matrix1, matrix2): #xin,xmax,ymin,ymax
    img_obj_shape = (int(max(matrix1[3], matrix2[3])-min(matrix1[2], matrix2[2])), 
                int(max(matrix1[1], matrix2[1])-min(matrix1[0], matrix2[0])))
    return img_obj_shape

def generate_union_bbox_shape(matrix_list): #xin,xmax,ymin,ymax
    matrix_array = np.array(matrix_list)
    img_obj_shape = (int(max(matrix_array[:,3]) - min(matrix_array[:,2])),
                     int(max(matrix_array[:,1]) - min(matrix_array[:,0])))
    return img_obj_shape

def get_union_bbox_left_top(matrix_list): #xin,xmax,ymin,ymax
    matrix_array = np.array(matrix_list)
    left_top = (int(min(matrix_array[:,0])),
                     int(min(matrix_array[:,2])))
    return left_top
def generate_union_bbox_(matrix_list):
    img_obj_shape = generate_union_bbox_shape(matrix_list)
    left_top = get_union_bbox_left_top(matrix_list)
    union_bbox = [int(left_top[0]), 
                  int(left_top[0]+int(img_obj_shape[1])),
                  int(left_top[1]),
                  int(left_top[1]+int(img_obj_shape[0]))]
    return union_bbox

def generate_new_bbox_within_distance(img_size, img_obj_size, old_bbox, scale=2.5):
    array_x = np.arange(int(img_size[1] - img_obj_size[1]))
    #array_y = np.arange(int(img_size[0] - img_obj_size[0])/3, int(img_size[0] - img_obj_size[0])/3*2)
    array_y = np.arange(max(0, int((old_bbox[3]+old_bbox[2])/2 - scale*img_obj_size[0])),
                        min(int((old_bbox[3]+old_bbox[2])/2 + scale*img_obj_size[0]), int(img_size[0] - img_obj_size[0])))
    random_x = random.sample(list(array_x), 1)[0]
    random_y = random.sample(list(array_y), 1)[0]
    new_position = (random_x, random_y)
    new_bbox = [random_x, random_x + img_obj_size[1], random_y, random_y + img_obj_size[0]]
    #print(new_bbox)
    return new_bbox

def check_before_insert(img_size, img_obj_size, etree, union_bbox):
    new_bbox = generate_new_bbox_within_distance(img_size, img_obj_size, union_bbox)
    bboxes = get_bboxes_from_etree(etree)
    retry_times = 0
    while(not check_bbox(new_bbox, bboxes)):
        print('new_bbox not suitable, retry...')
        retry_times = retry_times + 1
        if(retry_times > 100):
            return (False, False)
        new_bbox = generate_new_bbox_within_distance(img_size, img_obj_size, union_bbox)
    return (new_bbox[0], new_bbox[2])
    
def inset_obj_to_an_image_and_xml(img_obj, img, obj_element, etree):
    new_bbox = generate_new_bbox(img.shape[:2], img_obj.shape[:2])
    bboxes = get_bboxes_from_etree(etree)
    retry_times = 0
    while(not check_bbox(new_bbox, bboxes)):
        print('new_bbox not suitable, retry...')
        retry_times = retry_times + 1
        if(retry_times > 50):
            return False, False
        new_bbox = generate_new_bbox(img.shape[:2], img_obj.shape[:2])
    #print('new_bbox succussful')
    new_pil_img, new_xml_etree = past_and_insert(img_obj, img, (new_bbox[0], new_bbox[2]), obj_element, etree)
    
    return new_pil_img, new_xml_etree

def do_inset_obj_to_an_image_and_xml(img_obj, img, obj_element, etree, insert_point):
    new_pil_img, new_xml_etree = past_and_insert(img_obj, img, insert_point, obj_element, etree)    
    return new_pil_img, new_xml_etree

def inset_dobule_obj_to_an_image_and_xml(img_obj1, img_obj2, img, obj_element1, obj_element2, etree):
    new_bbox = generate_new_bbox(img.shape[:2], img_obj.shape[:2])
    bboxes = get_bboxes_from_etree(etree)
    retry_times = 0
    while(not check_bbox(new_bbox, bboxes)):
        print('new_bbox not suitable, retry...')
        retry_times = retry_times + 1
        if(retry_times > 50):
            return False, False
        new_bbox = generate_new_bbox(img.shape[:2], img_obj.shape[:2])
    #print('new_bbox succussful')
    new_pil_img, new_xml_etree = past_and_insert(img_obj, img, (new_bbox[0], new_bbox[2]), obj_element, etree)
    
    return new_pil_img, new_xml_etree

def check_bbox(new_bbox, bboxes):
    for bbox in bboxes:
        if(IOU(new_bbox, bbox) > 0):
            return False
    return True
def caculate_move_vector(bbox, new_point):
    original_xmin, original_ymin = bbox[0], bbox[2]
    diffx, diffy = new_point[0] - original_xmin, new_point[1] - original_ymin
    return (diffx, diffy)

def rotate_img(img, thealta):
    (h_, w_) = img.shape[:2]
    point_list = [(0, 0), (0, h_), (w_, h_), (w_, 0)]
    center = (w_ // 2, h_ // 2)
    roted_point_list = [((point[0]-center[0])*np.cos(np.pi*thealta/180) 
                         - (point[1]-center[1])*np.sin(np.pi*thealta/180) 
                         + center[0], (point[0]-center[0])*np.sin(np.pi*thealta/180) 
                         + (point[1]-center[1])*np.cos(np.pi*thealta/180) + center[1]) for point in point_list]
    #print(roted_point_list)

    temp = np.zeros((2, 4))
    temp[0] = [roted_point[0] for roted_point in roted_point_list]
    temp[1] = [roted_point[1] for roted_point in roted_point_list]
    (xmin, xmax, ymin, ymax) = (np.min(temp[0]), np.max(temp[0]), np.min(temp[1]), np.max(temp[1]))
    print('xmin: {0}, xmax: {1}, ymin: {2}, ymax: {3}'.format(xmin, xmax, ymin, ymax))

    roted_h, roted_w = ymax - ymin, xmax - xmin
    print('roted_h: {0}, roted_w: {1}'.format(roted_w, roted_h))
    
    top_bottom, left_right = int((roted_h - h_)/2), int((roted_w - w_)/2)
    print('top_bottom:{0}, left_right_:{1}'.format(top_bottom, left_right))
    padding = lambda arg : max(arg, 0)
    #dst = cv2.copyMakeBorder(img, padding(top_bottom), padding(top_bottom), padding(left_right), 
    #padding(left_right), cv2.BORDER_CONSTANT)
    dst = cv2.copyMakeBorder(img, padding(top_bottom), padding(top_bottom), padding(left_right), 
                             padding(left_right), cv2.BORDER_CONSTANT)
    
    (h, w) = dst.shape[:2]   
    center = (w // 2, h // 2)
    M = cv2.getRotationMatrix2D(center, thealta, 1.0)
    rotated_img = cv2.warpAffine(dst, M, (w, h))
    if(top_bottom < 0):
        top_bottom = abs(top_bottom)
        rotated_img = rotated_img[top_bottom:-top_bottom, :, :]
    if(left_right < 0):
        left_right = abs(left_right)
        rotated_img = rotated_img[:, left_right:-left_right, :]
    return rotated_img


In [2]:
############################# for person-intercouses (overlaps) ##################################
LOOP_TIMES = 1
REPEAT_TIMES = 5
seed_xml_names = os.listdir(SEED_XML_DIR)
seed_xml_names.sort()
cls_to_rotate = ['person']

for i in range (LOOP_TIMES):
    for xml_name in seed_xml_names:
        img_name = SEED_IMG_DIR + xml_name[:-3] + 'jpg'
        xml_name = SEED_XML_DIR + xml_name
        print(img_name)
        print(xml_name)
        
        tree=ET.parse(xml_name)
        img = cv2.imread(img_name)
        objs = get_obj_from_xml(xml_name)
        bboxes = get_bboxes_from_etree(tree)
        flag_found = False
        i = 0
        #------------------------------------------------------------
        bboxes_motorbike = {}
        bboxes_person = {}
        for obj_element in objs:
            bbox = get_bbox_from_xmlobj(obj_element)           
            img_obj = get_obj_from_image_file(img_name, bbox)

            cls = get_cls_from_xmlobj(obj_element)
            '''
            if (cls == 'motorbike'):
                bboxes_motorbike[(i)] = bbox
            '''
            if (cls == 'person'):
                bboxes_person[(i)] = bbox
            i = i + 1
        #caculate iou
        #print(bboxes_motorbike) 
        #print(bboxes_person)
        id_dic = {}
        ##------------------------------------------------##
        person_keys = bboxes_person.keys()
        person_bboxes = bboxes_person.values()
        person_keys_list = list(person_keys)
        person_bboxes_list = list(person_bboxes)
        #print(person_keys_list)
        #print(person_bboxes_list)
        _i = 0
        for _bbx in person_bboxes_list:
            _i = _i + 1
            id_list = []
            #for __bbx in person_bboxes_list[_i:]: ##forward
            for __bbx in person_bboxes_list:
                if(_bbx == __bbx): ##the same id
                    continue
                if(IOU(_bbx, __bbx) > 0.1):
                    id_list.append(person_keys_list[person_bboxes_list.index(__bbx)])
            id_dic[(person_keys_list[_i-1])] = id_list
        #print('id_dic:{0}'.format(id_dic))
        for k__, v__ in id_dic.items():
            for v_ in v__:
                if(len(id_dic[v_]) == 0):
                    continue
                id_dic[k__] = id_dic[k__] + id_dic[v_]
                id_dic[k__] = list(set(id_dic[k__]))
                id_dic[k__].sort()
        #print('id_dic:{0}'.format(id_dic))

        
        for __k in list(id_dic.keys()):
            if(len(id_dic[__k]) == 0):
                id_dic.pop(__k)
        
        #print('id_dic:{0}'.format(id_dic))
        
        v_list = []
        id_dic_refine = {}
        for __k, __v in id_dic.items():
            if(__k not in v_list):
                v_list = v_list + __v
                #print('k:{0};v_list:{1}'.format(__k, v_list))
                id_dic_refine[(__k)] = __v
                
        id_dic = id_dic_refine
        #print('id_dic:{0}'.format(id_dic))
        #continue;
        
        FLAG = False
        for i in range(REPEAT_TIMES):
            for kk, vv in id_dic.items():
                if(len(vv) == 0):
                    continue
                elif(len(vv) >= 1):
                    templist = [bboxes[v] for v in vv]
                    ##templist.append(bboxes[kk])
                    img_obj_shape = generate_union_bbox_shape(templist)
                    union_bbox = generate_union_bbox_(templist)
                    (xmin, ymin) = check_before_insert(img.shape[:2], img_obj_shape, tree, union_bbox)
                    if(xmin == False) or (ymin == False):
                        print("give up, try next bbox")
                        continue
                    (diffx, diffy) = caculate_move_vector(union_bbox, (xmin, ymin))
                    '''
                    new_p_kk = (int(bboxes[kk][0] + diffx), int(bboxes[kk][2] + diffy))
                    #print(new_p_kk)
                    img_obj = get_obj_from_image_file(img_name, bboxes[kk])
                    new_pil_img, new_xml_etree = past_and_insert(img_obj, img, new_p_kk, objs[kk], tree)
                    if((new_pil_img == False) or (new_xml_etree == False)):
                        continue
                    tree = new_xml_etree
                    img = np.array(new_pil_img)
                    '''
                    for v in vv:
                        new_left_top = (int(bboxes[v][0] + diffx), int(bboxes[v][2] + diffy))
                        img_obj = get_obj_from_image_file(img_name, bboxes[v])
                        new_pil_img, new_xml_etree = past_and_insert(img_obj, img, new_left_top, objs[v], tree)
                        if((new_pil_img == False) or (new_xml_etree == False)):
                            continue
                        tree = new_xml_etree
                        img = np.array(new_pil_img)
                        FLAG = True
            #------------------------------------------------------------
            '''
            i = 0
            for obj_element in objs:
                bbox = get_bbox_from_xmlobj(obj_element)           
                img_obj = get_obj_from_image_file(img_name, bbox)

                cls = get_cls_from_xmlobj(obj_element)

                if (cls in cls_to_rotate):
                    print(cls)
                    flag_found = True
                    if(cls == 'person'):
                        repeat_angles = [0, 0]
                    else:
                        repeat_angles = []
                    for thealta in repeat_angles:
                        img_obj = rotate_img(img_obj, thealta)
                        new_pil_img, new_xml_etree = inset_obj_to_an_image_and_xml(img_obj, img, obj_element, tree)
                        if((new_pil_img == False) or (new_xml_etree == False)):
                            continue
                        tree = new_xml_etree
                        img = np.array(new_pil_img)
            if(flag_found != True):
                continue
            '''
        ## save xml and img
        if(FLAG != True):
            continue
        time_mark = datetime.datetime.now()
        time_str = time_mark.strftime("%Y%m%d%H%M%S%f_")
        new_pil_img = Image.fromarray(img[:,:,(2,1,0)])
        new_pil_img.save(GENE_IMG_DIR + time_str + img_name.split('/')[-1])
        tree.write(GENE_XML_DIR + time_str + xml_name.split('/')[-1])
        
        #break
    #break        

/data/darknet/python/20190507_image/003010000.0.jpg
/data/darknet/python/20190507_xml/003010000.0.xml
(260, 167, 3)
(203, 110, 3)
(126, 63, 3)
(123, 66, 3)
(112, 72, 3)
(128, 46, 3)
(155, 826, 3)
(58, 48, 3)
(65, 37, 3)
(81, 32, 3)
(77, 37, 3)
(81, 34, 3)
(75, 27, 3)
(83, 33, 3)
(56, 31, 3)
(96, 266, 3)
[0, 1, 2, 4, 5, 7, 8, 9, 10, 11, 12, 13, 14]
[[489.0, 656.0, 547.0, 807.0], [634.0, 744.0, 326.0, 529.0], [471.0, 534.0, 118.0, 244.0], [385.0, 457.0, 149.0, 261.0], [549.0, 595.0, 108.0, 236.0], [334.0, 382.0, 135.0, 193.0], [47.0, 84.0, 94.0, 159.0], [192.0, 224.0, 66.0, 147.0], [435.0, 472.0, 137.0, 214.0], [151.0, 185.0, 50.0, 131.0], [247.0, 274.0, 67.0, 142.0], [257.0, 290.0, 67.0, 150.0], [217.0, 248.0, 44.0, 100.0]]
id_dic:{0: [], 1: [], 2: [], 4: [10], 5: [], 7: [], 8: [], 9: [], 10: [4], 11: [], 12: [13], 13: [12], 14: []}
k:4;v_list:[4, 10]
k:12;v_list:[4, 10, 12, 13]
new_bbox not suitable, retry...
(75, 27, 3)
(83, 33, 3)
(112, 72, 3)
(77, 37, 3)
new_bbox not suitable, retry

(122, 54, 3)
(119, 74, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(75, 35, 3)
(71, 33, 3)
(32, 27, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(65, 32, 3)
(71, 24, 3)
(154, 79, 3)
(122, 54, 3)
(119, 74, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(75, 35, 3)
(71, 33, 3)
(32, 27, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
give up, try next bbox
(154, 79, 3)
(122, 54, 3)
(119, 74, 3)
(75, 35, 3)
(71, 33, 3)
(32, 27, 3)
new_bbox not suitable, retry...
(65, 32, 3)
(71, 24, 3)
/data/darknet/python/20190507_image/003010010.0.jpg
/data/darknet/python/20190507_xml/003010010.0.xml
(142, 99, 3)
(288, 145, 3)
(144, 87, 3)
(231, 104, 3)
(155, 83, 3)
(71,

(138, 79, 3)
(68, 64, 3)
(156, 98, 3)
(153, 104, 3)
new_bbox not suitable, retry...
(138, 79, 3)
(68, 64, 3)
(156, 98, 3)
(153, 104, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(138, 79, 3)
(68, 64, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(156, 98, 3)
(153, 104, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(138, 79, 3)
(68, 64, 3)
/data/darknet/python/20190507_image/003010014.0.jpg
/data/darknet/python/20190507_xml/003010014.0.xml
(268, 121, 3)
(150, 78, 3)
(138, 69, 3)
(194, 88, 3)
(154, 87, 3)
(142, 66, 3)
(155, 96, 3)
(127, 70, 3)
(155, 707, 3)
(79, 47, 3)
(139, 145, 3)
(65, 44, 3)
(184, 145, 3)
(82, 37, 3)
(85, 31, 3)
(84, 39, 3)
(222, 55, 3)
(57, 34, 3)
(70, 

(162, 84, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(154, 85, 3)
(162, 84, 3)
/data/darknet/python/20190507_image/003010019.0.jpg
/data/darknet/python/20190507_xml/003010019.0.xml
(131, 73, 3)
(130, 68, 3)
(827, 1189, 3)
(114, 75, 3)
(77, 62, 3)
(223, 102, 3)
(62, 81, 3)
(77, 50, 3)
(183, 727, 3)
(248, 96, 3)
(179, 75, 3)
(72, 296, 3)
(67, 36, 3)
(28, 37, 3)
(85, 37, 3)
(67, 325, 3)
[0, 1, 3, 4, 5, 6, 7, 9, 10, 12, 13, 14]
[[596.0, 669.0, 163.0, 294.0], [417.0, 485.0, 123.0, 253.0], [1026.0, 1101.0, 213.0, 327.0], [712.0, 774.0, 231.0, 308.0], [1800.0, 1902.0, 521.0, 744.0], [911.0, 992.0, 233.0, 295.0], [555.0, 605.0, 227.0, 304.0], [1632.0, 1728.0, 562.0, 810.0], [1285.0, 1360.0, 196.0, 375.0], [862.0, 898.0, 1.0, 68.0], [671.0, 708.0, 1.0, 29.0], [74.0, 111.0, 67.0, 152.0]]
id_dic:{0: [], 1: [], 3: [], 4: [], 5: [], 6: [], 7: [], 9: [], 10: [], 12: [], 13: [], 14: []}
/data/darknet/python/20190507_image/003010020.0.jpg
/data/darknet/python/20190507_xml/00301

new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(79, 36, 3)
(73, 30, 3)
(74, 33, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(182, 83, 3)
(193, 98, 3)
/data/darknet/python/20190507_image/003010026.0.jpg
/data/darknet/python/20190507_xml/003010026.0.xml
(195, 113, 3)
(227, 620, 3)
(189, 87, 3)
(125, 76, 3)
(137, 85, 3)
(182, 86, 3)
(192, 105, 3)
(131, 92, 3)
(222, 107, 3)
(217, 96, 3)
(86, 34, 3)
(64, 29, 3)
(300, 129, 3)
(70, 332, 3)
(87, 46, 3)
(58, 46, 3)
(76, 32, 3)
(30, 37, 3)
(62, 29, 3)
[0, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 14, 15, 16,

...

(152, 83, 3)
(157, 83, 3)
(218, 540, 3)
(169, 77, 3)
(253, 579, 3)
(135, 308, 3)
(83, 330, 3)
(130, 82, 3)
(131, 332, 3)
(325, 949, 3)
(201, 41, 3)
(70, 37, 3)
(36, 269, 3)
(93, 340, 3)
(69, 43, 3)
(71, 37, 3)
(51, 34, 3)
[0, 1, 3, 16, 7, 10, 11, 14, 15]
[[687.0, 770.0, 232.0, 384.0], [578.0, 661.0, 237.0, 394.0], [774.0, 851.0, 221.0, 390.0], [529.0, 563.0, 65.0, 116.0], [934.0, 1016.0, 215.0, 345.0], [1878.0, 1919.0, 284.0, 485.0], [600.0, 637.0, 4.0, 74.0], [379.0, 422.0, 157.0, 226.0], [560.0, 597.0, 15.0, 86.0]]
id_dic:{0: [], 1: [], 3: [], 16: [], 7: [], 10: [], 11: [], 14: [], 15: []}
/data/darknet/python/20190507_image/003012111.0.jpg
/data/darknet/python/20190507_xml/003012111.0.xml
(151, 83, 3)
(157, 95, 3)
(217, 552, 3)
(247, 532, 3)
(168, 78, 3)
(138, 228, 3)
(141, 350, 3)
(72, 350, 3)
(77, 38, 3)
(118, 83, 3)
(36, 283, 3)
(63, 35, 3)
(390, 1010, 3)
(101, 334, 3)
(79, 38, 3)
(63, 27, 3)
[0, 1, 4, 8, 9, 11, 14, 15]
[[674.0, 757.0, 228.0, 379.0], [568.0, 663.0, 233.0, 390.0],

(154, 63, 3)
(131, 72, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(101, 58, 3)
(78, 44, 3)
(95, 65, 3)
new_bbox not suitable, retry...
(154, 63, 3)
(131, 72, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(101, 58, 3)
(78, 44, 3)
(95, 65, 3)
(154, 63, 3)
(131, 72, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(101, 58, 3)
(78, 44, 3)
(95, 65, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(154, 63, 3)
(131, 72, 3)
(101, 58, 3)
(78, 44, 3)
(95, 65, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(154, 63, 3)
(131, 72, 3)
/data/darknet/python/20190507_image/003012122.0.jpg
/data/darknet/python/20190507_xml/003012122.0.xml
(141, 77, 3)
(212, 556, 3)
(282, 418, 3)
(146, 60, 3)
(154, 61, 3)
(75, 42, 3)
(116, 69, 3)
(66, 38, 3)
(71,

(116, 58, 3)
new_bbox not suitable, retry...
(121, 65, 3)
(102, 55, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(67, 38, 3)
(94, 61, 3)
new_bbox not suitable, retry...
(138, 79, 3)
(116, 58, 3)
(121, 65, 3)
(102, 55, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(67, 38, 3)
(94, 61, 3)
new_bbox not suitable, retry...
(138, 79, 3)
(116, 58, 3)
new_bbox not suitable, retry...
(121, 65, 3)
(102, 55, 3)
new_bbox not suitable, retry...
(67, 38, 3)
(94, 61, 3)
(138, 79, 3)
(116, 58, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(121, 65, 3)
(102, 55, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(67, 38, 3)
(94, 61, 3)
/data/darknet/python/20190507_image/003012132.0.jpg
/data/darknet/python/20190507_xml/003012132.0.xml
(213, 535, 3)
(133, 73, 3)
(118

(105, 54, 3)
new_bbox not suitable, retry...
(75, 40, 3)
(77, 39, 3)
/data/darknet/python/20190507_image/003012139.0.jpg
/data/darknet/python/20190507_xml/003012139.0.xml
(218, 536, 3)
(112, 67, 3)
(127, 80, 3)
(118, 68, 3)
(93, 67, 3)
(73, 40, 3)
(67, 44, 3)
(56, 45, 3)
(35, 271, 3)
(71, 36, 3)
(100, 62, 3)
(100, 365, 3)
(57, 41, 3)
[1, 2, 3, 4, 5, 6, 7, 9, 10, 12]
[[445.0, 512.0, 118.0, 230.0], [500.0, 580.0, 167.0, 294.0], [553.0, 621.0, 119.0, 237.0], [456.0, 523.0, 214.0, 307.0], [544.0, 584.0, 35.0, 108.0], [593.0, 637.0, 5.0, 72.0], [339.0, 384.0, 143.0, 199.0], [637.0, 673.0, 12.0, 83.0], [519.0, 581.0, 118.0, 218.0], [213.0, 254.0, 131.0, 188.0]]
id_dic:{1: [], 2: [3, 4, 10], 3: [2, 10], 4: [2], 5: [], 6: [], 7: [], 9: [], 10: [2, 3], 12: []}
k:2;v_list:[2, 3, 4, 10]
(127, 80, 3)
(118, 68, 3)
(93, 67, 3)
(100, 62, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(127, 80, 3)
(118, 68, 3)
(93, 67, 3)
(100, 62, 3)
(127, 80, 3)
(118, 68, 3)
(93, 67, 3)
(100, 62,

(108, 58, 3)
(206, 145, 3)
(98, 359, 3)
(35, 268, 3)
(73, 32, 3)
(64, 28, 3)
[1, 2, 3, 4, 6, 8, 9, 12, 13]
[[417.0, 487.0, 141.0, 261.0], [462.0, 523.0, 115.0, 229.0], [521.0, 596.0, 184.0, 310.0], [485.0, 544.0, 218.0, 313.0], [358.0, 415.0, 118.0, 222.0], [553.0, 611.0, 111.0, 219.0], [1327.0, 1472.0, 817.0, 1023.0], [532.0, 564.0, 33.0, 106.0], [559.0, 587.0, 20.0, 84.0]]
id_dic:{1: [2], 2: [1], 3: [4, 8], 4: [3], 6: [], 8: [3], 9: [], 12: [], 13: []}
k:1;v_list:[1, 2]
k:3;v_list:[1, 2, 3, 4, 8]
(120, 70, 3)
(114, 61, 3)
(126, 75, 3)
(95, 59, 3)
(108, 58, 3)
(120, 70, 3)
(114, 61, 3)
(126, 75, 3)
(95, 59, 3)
(108, 58, 3)
(120, 70, 3)
(114, 61, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(126, 75, 3)
(95, 59, 3)
(108, 58, 3)
(120, 70, 3)
(114, 61, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
(126, 75, 3)
(95, 59, 3)
(108, 58, 3)
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not suitable, retry...
new_bbox not sui

In [ ]:
################################# for motorbike-person pairs  ######################################
LOOP_TIMES = 1
seed_xml_names = os.listdir(SEED_XML_DIR)
seed_xml_names.sort()
cls_to_rotate = ['person']

for i in range (LOOP_TIMES):
    for xml_name in seed_xml_names:
        img_name = SEED_IMG_DIR + xml_name[:-3] + 'jpg'
        xml_name = SEED_XML_DIR + xml_name
        print(img_name)
        print(xml_name)
        
        tree=ET.parse(xml_name)
        img = cv2.imread(img_name)
        objs = get_obj_from_xml(xml_name)
        bboxes = get_bboxes_from_etree(tree)
        flag_found = False
        i = 0
        #------------------------------------------------------------
        bboxes_motorbike = {}
        bboxes_person = {}
        for obj_element in objs:
            bbox = get_bbox_from_xmlobj(obj_element)           
            img_obj = get_obj_from_image_file(img_name, bbox)

            cls = get_cls_from_xmlobj(obj_element)
            if (cls == 'motorbike'):
                bboxes_motorbike[(i)] = bbox
            if (cls == 'person'):
                bboxes_person[(i)] = bbox
            i = i + 1
        #caculate iou
        #print(bboxes_motorbike) 
        #print(bboxes_person)
        id_dic = {}
        for key, val in bboxes_motorbike.items():
            id_list = []
            for k, v in bboxes_person.items():
                if(IOU(val, v) > 0.2):
                    id_list.append(k)
                    
                    #print(val)
                    #print(v)
            id_dic[(key)] = id_list
        print(id_dic)
        REPEAT_TIMES = 3
        FLAG = False
        for i in range(REPEAT_TIMES):
            for kk, vv in id_dic.items():
                if(len(vv) != 1):
                    continue
                else:
                    #print(bboxes_motorbike[kk])
                    #print(bboxes[kk])
                    #print(bboxes_person[vv[0]])
                    #print(bboxes[vv[0]])
                    img_obj_shape = generate_union_bbox(bboxes[kk], bboxes[vv[0]])
                    union_bbox_letf_top = (int(min(bboxes[kk][0], bboxes[vv[0]][0])), 
                                           int(min(bboxes[kk][2], bboxes[vv[0]][2])))
                    union_bbox = [int(min(bboxes[kk][0], bboxes[vv[0]][0])), 
                                  int(min(bboxes[kk][0], bboxes[vv[0]][0]))+int(img_obj_shape[1]),
                                  int(min(bboxes[kk][2], bboxes[vv[0]][2])),
                                  int(min(bboxes[kk][2], bboxes[vv[0]][2]))+int(img_obj_shape[0])]
                    (xmin, ymin) = check_before_insert(img.shape[:2], img_obj_shape, tree, union_bbox)
                    if(xmin == False) or (ymin == False):
                        print("give up, try next bbox")
                        continue
                    (diffx, diffy) = caculate_move_vector(union_bbox, (xmin, ymin))
                    new_p_vv = (int(bboxes[vv[0]][0] + diffx), int(bboxes[vv[0]][2] + diffy))
                    #print(new_p_vv)
                    new_p_kk = (int(bboxes[kk][0] + diffx), int(bboxes[kk][2] + diffy))
                    #print(new_p_kk)
                    img_obj = get_obj_from_image_file(img_name, bboxes[kk])
                    new_pil_img, new_xml_etree = past_and_insert(img_obj, img, new_p_kk, objs[kk], tree)
                    if((new_pil_img == False) or (new_xml_etree == False)):
                        continue
                    tree = new_xml_etree
                    img = np.array(new_pil_img)
                    img_obj = get_obj_from_image_file(img_name, bboxes[vv[0]])
                    new_pil_img, new_xml_etree = past_and_insert(img_obj, img, new_p_vv, objs[vv[0]], tree)
                    if((new_pil_img == False) or (new_xml_etree == False)):
                        continue
                    tree = new_xml_etree
                    img = np.array(new_pil_img)
                    FLAG = True
            #break                
            #------------------------------------------------------------
            '''
            i = 0
            for obj_element in objs:
                bbox = get_bbox_from_xmlobj(obj_element)           
                img_obj = get_obj_from_image_file(img_name, bbox)

                cls = get_cls_from_xmlobj(obj_element)

                if (cls in cls_to_rotate):
                    print(cls)
                    flag_found = True
                    if(cls == 'person'):
                        repeat_angles = [0, 0]
                    else:
                        repeat_angles = []
                    for thealta in repeat_angles:
                        img_obj = rotate_img(img_obj, thealta)
                        new_pil_img, new_xml_etree = inset_obj_to_an_image_and_xml(img_obj, img, obj_element, tree)
                        if((new_pil_img == False) or (new_xml_etree == False)):
                            continue
                        tree = new_xml_etree
                        img = np.array(new_pil_img)
            if(flag_found != True):
                continue
            '''
        ## save xml and img
        if(FLAG != True):
            continue
        time_mark = datetime.datetime.now()
        time_str = time_mark.strftime("%Y%m%d%H%M%S%f_")
        new_pil_img = Image.fromarray(img[:,:,(2,1,0)])
        new_pil_img.save(GENE_IMG_DIR + time_str + img_name.split('/')[-1])
        tree.write(GENE_XML_DIR + time_str + xml_name.split('/')[-1])
        #break
        